In [1]:
import os
import sys
import six
import glob
import math
import pandas as pd
import numpy as np
from keras.utils import to_categorical
import scipy.ndimage as nd
from scipy.ndimage import zoom
import random

Using TensorFlow backend.


In [2]:
import keras
import tensorflow as tf
from keras import Model
from keras import backend as K
from keras.regularizers import l2
from keras.engine import Layer,InputSpec
from keras.layers.merge import concatenate
from keras.callbacks import TensorBoard,Callback
from keras.layers.advanced_activations import LeakyReLU
from keras.preprocessing.image import ImageDataGenerator
from keras.layers.normalization import BatchNormalization
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
from keras import initializers, regularizers, constraints,optimizers
from keras.callbacks import ModelCheckpoint, LearningRateScheduler,TensorBoard
from keras.layers import Add,Input,Conv3D,Convolution3D,Dropout,UpSampling3D,Concatenate,MaxPooling3D,\
GlobalAveragePooling3D,Dense,GlobalMaxPooling3D,Lambda,Activation,Reshape,Permute, PReLU, Deconvolution3D,Multiply,GlobalAveragePooling3D,Dense

In [3]:
sys.path.append('../baseLayers/')

In [4]:
from InstanceNorm import InstanceNormalization
from HRmodel import HRSegNet

In [5]:
num_blocks = 5
strides = [1,2,2,2,2]
nodule_seg_strides = [1,2,2,2,2]
atrous_rates = [1,1,1,1,1]
base_filters = 32
norm_func = InstanceNormalization
activation_func = LeakyReLU
kernel_size = 3
padding = 'same'
dropout_rate = 0
input_shape = (32,64,64,1)
num_classes = 4
kernel_initializer = 'he_normal'
kernel_regularizer = None
deep_supervision = True
ACF_choice = False
aux_task = False
SEB_choice = True
classification_layers = GlobalMaxPooling3D

In [6]:
sys.path.append('../../utils/')
from RWconfig import LoadJson,WriteJson

In [7]:
hrnet_config = {
    'activation_func':activation_func,
    'padding':padding,
    'kernel_initializer':kernel_initializer,
    'kernel_regularizer':kernel_regularizer,
    'num_classes':num_classes,
    'classification_layers':classification_layers,
    'dropout_rate':dropout_rate,
    "inchannels":base_filters*2,
    "norm_func":norm_func,
    'initial_strides':[1,2],
    'num_modules':1,
    'num_branches':[2,3,4],
    'block_per_stage':[3,3,2],
    'block_func':'BASIC',
    'FUSE_METHOD':'SUM'
    
    
}

In [8]:
hrseg_obj_2 = HRSegNet(**hrnet_config)
patch_size = 64
model_1 = hrseg_obj_2.get_model(input_shape=input_shape,stages=4,choice='upsample',merge_choice=True)

In [9]:
from ResNet import Resnet3DBuilder
from VGGmodel import VGG
from NoduleSegEncoder import NoduleSegEncoder_proxima


In [10]:
from CommonLayers import *
# from NoduleSegDecoder import NoduleSegDecoder_proxima
sys.path.append('../decoders/')
from NoduleSegDecoder import NoduleSegDecoder_proxima

In [11]:
model_1[1]

[<tf.Tensor 'main_input:0' shape=(?, 32, 64, 64, 1) dtype=float32>,
 <tf.Tensor 'add_36/add:0' shape=(?, 16, 32, 32, 64) dtype=float32>,
 <tf.Tensor 'add_39/add:0' shape=(?, 8, 16, 16, 128) dtype=float32>,
 <tf.Tensor 'add_42/add:0' shape=(?, 4, 8, 8, 256) dtype=float32>,
 <tf.Tensor 'add_45/add:0' shape=(?, 2, 4, 4, 512) dtype=float32>]

In [13]:
# model2 = NoduleSegDecoder_proxima(model_1,**noduleseg_decoder_parameter_list)

In [ ]:
model_1[0].summary()

In [ ]:
Total params: 72,390,658
Trainable params: 72,374,786
Non-trainable params: 15,872